# Examples from the discrete world

The purpose of this notebook is to test our general methodology in a very basic setting. In this sense, 
1. we will assume a model in a discrete setting (e.g., a basic binomial model); 
2. we will generate the needed data from that model and "assume" we don't know from which model this data comes from;
3. and try to solve the problem for this data.

## 1. Create the model

In [1]:
from robust_pricing.path_generators import BinomialTree, Uniform, Gaussian

In [44]:
granularity=20
path_length=20

model = BinomialTree(
    path_length=path_length,
    mean=100,
    up_factor=1.01,
    down_factor=0.99,
    granularity=100,
    observed_times=[i * (granularity // path_length) for i in range(1, path_length + 1)],
)

def hist_2d(data, time_1=0, time_2=1):
    import plotly.express as px
    import pandas as pd
    df = pd.DataFrame(data, columns = [f'S_{i+1}'for i in range(path_length)])
    fig = px.density_heatmap(df, x=f'S_{time_1 + 1}', y=f'S_{time_2 + 1}', marginal_x="histogram", marginal_y="histogram", nbinsx=80, nbinsy=80)
    fig.show()

In [45]:
data = model(10000).numpy()

In [48]:
hist_2d(data, 2, 19)

## 2. Create the inputs

In [49]:
%reload_ext autoreload
%autoreload 2
from robust_pricing.deePricing import *
from helper import *

## 2.1 The option portfolios

Based on this model, we need to create the base set of options $\mathcal{B}_t$ from which our (optimization) model will try to learn the model (probability measure) from which they come. For this task, we use the fact that we can sample from this model to price them using Monte-Carlo.

In [50]:
strike_prices = list(range(80, 130, 5))
pricing_data = model(10000)

option_portfolios = []

for t in range(path_length):
    calls = []
    puts = []
    for k in strike_prices:
        c = Call(strike=k, price=0)
        c.price = float(torch.mean(c(pricing_data[:, t])))
        p = Put(strike=k, price=0)
        p.price = float(torch.mean(p(pricing_data[:, t])))
        calls.append(c)
        puts.append(p)

    option_portfolios.append(
        OneMaturityOptionPortfolio(calls=calls, puts=puts)
    )
option_portfolio = DiagonalOptionPortfolio(option_portfolios)

## 2.2 The exotic option

In this case we will use a Lookback and/or Asian options:

In [61]:
K = 100
def f(x):
    return torch.relu(torch.mean(x, 1) - K)


K = 100
def f(x):
    return torch.relu(x.select(1,-1) - K)

Since we know the "right" model, we can use it to price the option using Monte-Carlo.

In [62]:
torch.mean(f(pricing_data))

tensor(1.7654)

## 2.3 We need to choose a model $\theta$ to sample from

In [63]:
# gm = Uniform(h.time_horizon, mean=model.mean, variance=20 ** 2)
gm = model
data = gm(10000)

In [72]:

hist_2d(data, 10, 19)

## 2.4 Create the hedging strategies

## 2.5 Optimize

In [93]:
from copy import deepcopy

number_of_observations=500
gamma = 401
no_trading_strategy = False
number_of_episodes = 4000


option_portfolio.reset_weights(zeros=False)

h_sup = HedgingStrategy(
    option_portfolio=deepcopy(option_portfolio),
    target_function=f,
    super_hedge=True,
    trading_kwargs=dict(num_layers=5, width_layers=100),
    no_trading_strategy=no_trading_strategy
)
h_sub = HedgingStrategy(
    option_portfolio=deepcopy(option_portfolio),
    target_function=f,
    super_hedge=False,
    trading_kwargs=dict(num_layers=5, width_layers=100),
    no_trading_strategy=no_trading_strategy    
)


h_sup.penalization_function.gamma = gamma
h_sub.penalization_function.gamma = gamma


h_sup.reset_weights(zeros=True)
h_sup.optimize(
    generator=gm, 
    number_of_observations=number_of_observations, 
    number_of_episodes=number_of_episodes,
)

h_sub.reset_weights(zeros=True)
h_sub.optimize(
    generator=gm, 
    number_of_observations=number_of_observations, 
    number_of_episodes=number_of_episodes,
)

In [94]:
from math import prod
s = 0
for par in h_sup.parameters():
    s += prod(list(par.shape))
s

215119

In [95]:
h_sup.visualize_training_status()

In [96]:
h_sub.visualize_training_status()

## 2.6 "Validate"

Since in this example, we have the actual model from which the option prices come from, we can estimate the replication error against that model.

In [97]:
print(h_sup.replication_error(model(1000)))
print(h_sub.replication_error(model(1000)))

tensor(0.0008, grad_fn=<MeanBackward0>)
tensor(0.6501, grad_fn=<MeanBackward0>)


We can print the upper and lower bound for the option price given the observed prices:

In [98]:
print(f'Upper bound: {h_sup.value}')
print(f'Actual bound: {torch.mean(f(pricing_data))}')
print(f'Lower bound: {h_sub.value}')

Upper bound: 2.332442283630371
Actual bound: 1.765406847000122
Lower bound: 1.5672829151153564


## 3. Let's evaluate the impact of $\gamma$

Recall that the objective function we are minimizing penalizes the sup/sub-hedging constraint with a penalization function $\beta:\mathbb{R}\to\mathbb{R}_+$. In this example we are using 

$$ \beta(x) = \frac{1}{p}(\max\{x, 0 \})^p,$$
with $p=2$. For any penalization function $\beta$, we define and we define $\beta_\gamma:\mathbb{R}\to\mathbb{R}_+$

$$\beta_\gamma(x)=\frac{1}{\gamma}\beta(\gamma x).$$

In [31]:
run_for_gammas_in(
    generator=model, 
    test_data=model(1000),
    option_portfolio=option_portfolio,
    target_function=f,
    low=1, 
    high=41,
    step=1, 
    number_of_observations=1000, 
    number_of_episodes=1000
)

KeyboardInterrupt: 

In [ ]:
import plotly.graph_objects as go
# Create traces
fig = go.Figure()
x = gammas

fig.add_trace(go.Scatter(
    x=gammas,
    y=sub_replication_error,
    mode='lines',
    name='sub_replication_error')
)

fig.add_trace(go.Scatter(
    x=gammas,
    y=sup_replication_error,
    mode='lines',
    name='sup_replication_error')
)

fig.update_layout(
    title="",
    xaxis_title=r"$\gamma$",
    yaxis_title=f"Replication error",
    legend_title="Bounds",

)

fig.show()

In [ ]:
# Create traces
fig = go.Figure()
x = gammas 

fig.add_trace(go.Scatter(
    x=gammas,
    y=lower_bound,
    mode='lines',
    name='lower_bound')
)

fig.add_trace(go.Scatter(
    x=gammas,
    y=upper_bound,
    mode='lines',
    name='upper_bound')
)

fig.update_layout(
    title="",
    xaxis_title=r"$\gamma$",
    yaxis_title=f"Solution",
    legend_title="Bounds",

)

fig.show()


## References
[1] Guo, G., & Obłój, J. (2019). Computational methods for martingale optimal transport problems. Annals of Applied Probability, 29(6), 3311–3347. https://doi.org/10.1214/19-AAP1481